In [3]:
import os
import pandas as pd
import plotly.express as px

#data path
data_folder = r"C:\Users\Dell\Downloads\archive (8)\cleaned_dataset\data"
metadata_path = r"C:\Users\Dell\Downloads\archive (8)\cleaned_dataset\metadata.csv"


metadata = pd.read_csv(metadata_path)

# Normalize 
metadata['filename'] = metadata['filename'].str.strip().str.lower()

# Initialize list 
all_data = []

# Load and combine cycle data with metadata
for file in os.listdir(data_folder):
    if file.endswith('.csv'):
        # Normalize current filename
        filename = os.path.basename(file).strip().lower()
        
      
        meta_row = metadata[metadata['filename'] == filename]
        if meta_row.empty:
            print(f"File {filename} not found in metadata. Skipping.")
            continue
        
        # Read cycle data
        file_path = os.path.join(data_folder, file)
        cycle_data = pd.read_csv(file_path)
        
        # Add metadata to cycle data
        for col in meta_row.columns:
            cycle_data[col] = meta_row[col].values[0]
        
        all_data.append(cycle_data)

# Combine 
combined_data = pd.concat(all_data, ignore_index=True)

# Handle missing values for Re and Rct
combined_data['Re'] = pd.to_numeric(combined_data['Re'], errors='coerce')
combined_data['Rct'] = pd.to_numeric(combined_data['Rct'], errors='coerce')

# To check if  UID exists and is numeric
if 'uid' not in combined_data.columns or not pd.api.types.is_numeric_dtype(combined_data['uid']):
    combined_data['uid'] = combined_data.index

# if they are Re and Rct not null
print("Non-NaN Re values:", combined_data['Re'].notna().sum())
print("Non-NaN Rct values:", combined_data['Rct'].notna().sum())

# Create for different type values 
discharge_data = combined_data[
    (combined_data['type'] == 'discharge') & 
    (combined_data['Re'].notna() | combined_data['Rct'].notna())
]
charge_data = combined_data[
    (combined_data['type'] == 'charge') & 
    (combined_data['Re'].notna() | combined_data['Rct'].notna())
]
impedance_data = combined_data[
    (combined_data['type'] == 'impedance') & 
    (combined_data['Rct'].notna())
]

# check , no of values of these categorical values 
print(f"Discharge data points: {len(discharge_data)}")
print(f"Charge data points: {len(charge_data)}")
print(f"Impedance data points: {len(impedance_data)}")

# Plot Re over cycles for discharge
if not discharge_data.empty:
    fig_re = px.line(
        discharge_data,
        x='uid',
        y='Re',
        title='Electrolyte Resistance (Re) Over Discharge Cycles',
        labels={'uid': 'Cycle (UID)', 'Re': 'Electrolyte Resistance (Ohms)'}
    )
    fig_re.update_traces(mode='lines+markers')
    fig_re.show()
else:
    print("No data available for Re in discharge cycles.")

# Plot Rct over cycles for discharge
if not discharge_data.empty:
    fig_rct = px.line(
        discharge_data,
        x='uid',
        y='Rct',
        title='Charge Transfer Resistance (Rct) Over Discharge Cycles',
        labels={'uid': 'Cycle (UID)', 'Rct': 'Charge Transfer Resistance (Ohms)'}
    )
    fig_rct.update_traces(mode='lines+markers')
    fig_rct.show()
else:
    print("No data available for Rct in discharge cycles.")
    
# Plot Re over cycles for charge
if not charge_data.empty:
    fig_re_charge = px.line(
        charge_data,
        x='uid',
        y='Re',
        title='Electrolyte Resistance (Re) Over Charge Cycles',
        labels={'uid': 'Cycle (UID)', 'Re': 'Electrolyte Resistance (Ohms)'}
    )
    fig_re_charge.update_traces(mode='lines+markers')
    fig_re_charge.show()
else:
    print("No data available for Re in charge cycles.")

# Plot Rct over cycles for charge
if not charge_data.empty:
    fig_rct_charge = px.line(
        charge_data,
        x='uid',
        y='Rct',
        title='Charge Transfer Resistance (Rct) Over Charge Cycles',
        labels={'uid': 'Cycle (UID)', 'Rct': 'Charge Transfer Resistance (Ohms)'}
    )
    fig_rct_charge.update_traces(mode='lines+markers')
    fig_rct_charge.show()
else:
    print("No data available for Rct in charge cycles.")


# Plot Battery Impedance (Rct for impedance tests)
if not impedance_data.empty:
    fig_impedance = px.line(
        impedance_data,
        x='uid',
        y='Rct',
        title='Battery Impedance (Rct) Over Cycles',
        labels={'uid': 'Cycle (UID)', 'Rct': 'Impedance (Ohms)'}
    )
    fig_impedance.update_traces(mode='lines+markers')
    fig_impedance.show()
else:
    print("No data available for impedance cycles.")


Non-NaN Re values: 93456
Non-NaN Rct values: 93456
Discharge data points: 0
Charge data points: 0
Impedance data points: 93456
No data available for Re in discharge cycles.
No data available for Rct in discharge cycles.
No data available for Re in charge cycles.
No data available for Rct in charge cycles.
